In [1]:
import pandas as pd
from tqdm.notebook import tqdm
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.pyplot import rcParams
import matplotlib as mpl
import seaborn as sns
import pickle as pkl
import itertools as it
from functools import reduce
import scanpy as sc
import scipy
from nero import Harmonia

In [2]:
prefix = '/data/comet.tmp/'

In [3]:
sc.settings.verbosity = 4
sc.settings.set_figure_params(dpi=80)
print(sc.__version__)
sc.settings.n_jobs=8

1.5.1


In [4]:
concat = sc.read_h5ad(prefix + 'concat.gene.filt.singlets.trans.scale.pca.dimred.clust.h5ad')

Because the freemuxlet outputs were merged across the well for each pool, `pool_clust` should define each individual sample.

In [7]:
concat.obs['pool_clust'] = concat.obs['pool'].astype(str) + '_' + concat.obs['BEST.GUESS'].astype(str)

In [9]:
covars = pd.read_csv(prefix + 'csvs/covars.csv', index_col=0)

In [10]:
declined_pts = #<redacted>

In [22]:
regex_str = '|'.join(declined_pts)

In [25]:
covars = covars[~covars['donor'].str.contains(r'%s' % regex_str)]

In [26]:
covars.set_index('pool_clust', inplace=True)

In [27]:
for covar in covars.columns:
    new_covar = list()
    for bc in concat.obs_names:
        try:
            new_covar.append(covars.loc[concat.obs.loc[bc, 'pool_clust'], covar])
        except KeyError:
            new_covar.append(concat.obs.loc[bc, 'pool_clust'])
    print('done with %s' % covar)
    concat.obs[covar] = new_covar

done with freemux_cluster
done with donor
done with timepoint
done with admission_level
done with respiratory_support_D0
done with onset_to_D0_days
done with intubated_days
done with admission_to_discharge
done with D0_to_death
done with race
done with sex
done with ethnicity
done with consent
done with COVID_status
done with death 
done with pulmonary_infection
done with non_pulmonary_infection
done with pool


In [ ]:
# concat.obs.to_csv(prefix + 'csvs/concat.obs.csv')

concat_obs = pd.read_csv(prefix + 'csvs/concat.obs.csv', index_col=0)
concat.obs = concat_obs.copy()

In [ ]:
consented_concat = concat[concat.obs['COVID_status'].isin(covars['COVID_status'].value_counts().index.tolist())].copy()

In [84]:
consented_concat.write_h5ad(prefix + 'concat.gene.filt.singlets.trans.scale.pca.dimred.clust.consent.h5ad')